In [1]:
from __future__ import absolute_import
from __future__ import division 
from __future__ import print_function 

import numpy as np
import tensorflow as tf

tf.logging.set_verbosity(tf.logging.INFO)

In [29]:
def cnn_model_fn(features, labels, mode):
    """ Model fn for CNN"""

    # Input layer
    input_layer = tf.reshape(features["x"], [-1, 28, 28, 1])

    # Convolutional layer #1
    conv1 = tf.layers.conv2d(
        inputs=input_layer,
        filters=32,
        kernel_size=[5, 5],
        padding="same",
        activation=tf.nn.relu)

    # Pooling lyaer #1
    pool1 = tf.layers.max_pooling2d(inputs=conv1, pool_size=[2, 2], strides=2)

    # Second conv + pooling layers
    conv2 = tf.layers.conv2d(
        inputs=pool1,
        filters=64,
        kernel_size=[5, 5],
        padding="same",
        activation=tf.nn.relu)
    pool2 = tf.layers.max_pooling2d(inputs=conv2, pool_size=[2, 2], strides=2)

    # Dense layer
    pool2_flat = tf.reshape(pool2, [-1, 7 * 7 * 64])
    dense = tf.layers.dense(
        inputs=pool2_flat, units=1024, activation=tf.nn.relu)
    dropout = tf.layers.dropout(
        inputs=dense, rate=0.4, training=(mode == tf.estimator.ModeKeys.TRAIN))

    # Logits layer
    logits = tf.layers.dense(inputs=dropout, units=10)

    predictions = {
        "classes": tf.argmax(input=logits, axis=1),
        "probabilities": tf.nn.softmax(logits, name="softmax_tensor")
    }

    if mode == tf.estimator.ModeKeys.PREDICT:
        return tf.estimator.EstimatorSpec(mode=mode, predictions=predictions)

    # Compute loss
    loss = tf.losses.sparse_softmax_cross_entropy(labels=labels, logits=logits)

    if mode == tf.estimator.ModeKeys.TRAIN:
        optimizer = tf.train.GradientDescentOptimizer(learning_rate=0.001)
        train_op = optimizer.minimize(
            loss=loss, global_step=tf.train.get_global_step())
        return tf.estimator.EstimatorSpec(
            mode=mode, loss=loss, train_op=train_op)

    eval_metric_ops = {
        "accuracy":
        tf.metrics.accuracy(labels=labels, predictions=predictions["classes"])
    }
    return tf.estimator.EstimatorSpec(
        mode=mode, loss=loss, eval_metric_ops=eval_metric_ops)

In [30]:
# Load data
mnist = tf.contrib.learn.datasets.load_dataset("mnist")
train_data = mnist.train.images # Returns np.array
train_labels = np.asarray(mnist.train.labels, dtype=np.int32)
eval_data = mnist.test.images # Returns np.array
eval_labels = np.asarray(mnist.test.labels, dtype=np.int32)

Extracting MNIST-data/train-images-idx3-ubyte.gz
Extracting MNIST-data/train-labels-idx1-ubyte.gz
Extracting MNIST-data/t10k-images-idx3-ubyte.gz
Extracting MNIST-data/t10k-labels-idx1-ubyte.gz


In [31]:
mnist_classifier = tf.estimator.Estimator(
    model_fn=cnn_model_fn, model_dir="tmp/mnist_convnet_model")

tensors_to_log = {"probabilities": "softmax_tensor"}
logging_hook = tf.train.LoggingTensorHook(
    tensors=tensors_to_log, every_n_iter=50)

INFO:tensorflow:Using default config.
INFO:tensorflow:Using config: {'_model_dir': 'tmp/mnist_convnet_model', '_tf_random_seed': None, '_save_summary_steps': 100, '_save_checkpoints_steps': None, '_save_checkpoints_secs': 600, '_session_config': allow_soft_placement: true
graph_options {
  rewrite_options {
    meta_optimizer_iterations: ONE
  }
}
, '_keep_checkpoint_max': 5, '_keep_checkpoint_every_n_hours': 10000, '_log_step_count_steps': 100, '_train_distribute': None, '_device_fn': None, '_protocol': None, '_eval_distribute': None, '_experimental_distribute': None, '_service': None, '_cluster_spec': <tensorflow.python.training.server_lib.ClusterSpec object at 0x135fdbcf8>, '_task_type': 'worker', '_task_id': 0, '_global_id_in_cluster': 0, '_master': '', '_evaluation_master': '', '_is_chief': True, '_num_ps_replicas': 0, '_num_worker_replicas': 1}


In [32]:
train_input_fn = tf.estimator.inputs.numpy_input_fn(
    x={"x": train_data},
    y=train_labels,
    batch_size=100,
    num_epochs=None,
    shuffle=True)

mnist_classifier.train(
    input_fn=train_input_fn, steps=20000, hooks=[logging_hook])

INFO:tensorflow:Calling model_fn.
INFO:tensorflow:Done calling model_fn.
INFO:tensorflow:Create CheckpointSaverHook.
INFO:tensorflow:Graph was finalized.
INFO:tensorflow:Restoring parameters from tmp/mnist_convnet_model/model.ckpt-20000
INFO:tensorflow:Running local_init_op.
INFO:tensorflow:Done running local_init_op.
INFO:tensorflow:Saving checkpoints for 20000 into tmp/mnist_convnet_model/model.ckpt.
INFO:tensorflow:probabilities = [[0.01265547 0.00002597 0.00176698 0.00002211 0.0001105  0.00052592
  0.94500774 0.00000031 0.03979849 0.0000866 ]
 [0.00029473 0.0008503  0.02312491 0.00804363 0.00084115 0.00149901
  0.00763428 0.00001017 0.9573149  0.00038687]
 [0.00009319 0.00000029 0.00000732 0.00002476 0.9902002  0.00003154
  0.00195846 0.00034763 0.00579571 0.00154103]
 [0.00000063 0.98994035 0.0001678  0.00521996 0.00022239 0.00007036
  0.00005752 0.00075192 0.00331613 0.00025295]
 [0.0000004  0.99915755 0.00007243 0.00007924 0.00000672 0.0000055
  0.00002108 0.00000102 0.00065488 

INFO:tensorflow:loss = 0.09757207, step = 20001
INFO:tensorflow:probabilities = [[0.00019406 0.9879246  0.00403537 0.00075233 0.00229685 0.00005457
  0.00023584 0.00209433 0.00193738 0.00047482]
 [0.00000031 0.00000049 0.00015543 0.9648577  0.00000228 0.0001397
  0.00000003 0.0000002  0.0345384  0.00030541]
 [0.01347633 0.00010932 0.02322623 0.00054807 0.08608986 0.2971917
  0.5753788  0.00010283 0.00351934 0.00035752]
 [0.00000485 0.00000064 0.00118036 0.0029201  0.00000005 0.00000019
  0.         0.9859228  0.00000168 0.00996927]
 [0.9995796  0.         0.00001258 0.00000037 0.00000038 0.00019945
  0.00000145 0.00000402 0.00002309 0.00017904]
 [0.00000008 0.00012209 0.00063126 0.00072257 0.00008638 0.00074612
  0.00001567 0.00000276 0.9974956  0.00017745]
 [0.00000046 0.00001405 0.00005293 0.00207631 0.00002541 0.00005514
  0.00000001 0.98909134 0.00002603 0.00865848]
 [0.99920976 0.00000003 0.00002186 0.00000065 0.00000034 0.00074155
  0.0000173  0.00000044 0.0000052  0.00000282]
 [

INFO:tensorflow:global_step/sec: 11.8224
INFO:tensorflow:probabilities = [[0.0041757  0.00008955 0.00002492 0.010359   0.0000002  0.9850358
  0.00000325 0.00019781 0.00009819 0.00001556]
 [0.00000017 0.00027932 0.00475868 0.9734403  0.00017292 0.00064519
  0.00001865 0.00000198 0.02066645 0.00001636]
 [0.00017872 0.00007874 0.0002601  0.00248212 0.00001511 0.00035655
  0.00001945 0.00000149 0.99634176 0.00026593]
 [0.00267455 0.8396549  0.00183    0.00058719 0.00017225 0.00697173
  0.13509148 0.00052708 0.01246429 0.00002648]
 [0.00000033 0.00000005 0.00000002 0.00002133 0.9146043  0.00579015
  0.0000002  0.00261094 0.01981213 0.05716051]
 [0.00000152 0.00000054 0.00004481 0.9987091  0.00000068 0.00049969
  0.         0.00000093 0.00047231 0.00027038]
 [0.00140847 0.00883364 0.00579361 0.01690557 0.0044843  0.7282617
  0.18707888 0.0007677  0.0294993  0.01696675]
 [0.00000005 0.00891519 0.9640024  0.02673789 0.00000059 0.00001388
  0.00001457 0.00020152 0.00011356 0.0000003 ]
 [0.00000

INFO:tensorflow:loss = 0.050472144, step = 20101 (8.460 sec)
INFO:tensorflow:probabilities = [[0.9999503  0.         0.00000283 0.00000008 0.0000004  0.00000816
  0.00000555 0.00000002 0.00002544 0.00000734]
 [0.00000076 0.99543023 0.00003939 0.00143754 0.00048967 0.00003256
  0.00001279 0.00033668 0.00075766 0.00146273]
 [0.00001142 0.00025673 0.00285012 0.00196893 0.95258594 0.0001699
  0.00003023 0.02282002 0.00692241 0.01238421]
 [0.00000006 0.         0.00000168 0.00000001 0.99883515 0.00001451
  0.00017048 0.00000001 0.00096937 0.00000862]
 [0.00002595 0.9913756  0.00124952 0.0023158  0.00052125 0.00011083
  0.00038163 0.00249135 0.00085375 0.00067433]
 [0.00194478 0.00000525 0.00001978 0.00944994 0.00000624 0.98735213
  0.00000057 0.00001426 0.00090083 0.00030625]
 [0.9999968  0.         0.0000005  0.00000002 0.         0.00000152
  0.00000104 0.00000001 0.00000008 0.00000007]
 [0.00001274 0.00000007 0.00000031 0.0000481  0.00000029 0.99992085
  0.00000179 0.00000002 0.00001553 

INFO:tensorflow:global_step/sec: 11.9146
INFO:tensorflow:probabilities = [[0.00000001 0.00000177 0.99994206 0.0000495  0.00000155 0.00000002
  0.00000004 0.00000193 0.00000315 0.00000002]
 [0.00004649 0.0000234  0.9987469  0.00034156 0.00028036 0.00019188
  0.00005042 0.0000023  0.00031668 0.00000011]
 [0.0003994  0.00054765 0.00063129 0.01424687 0.00006107 0.0086026
  0.00052834 0.00002999 0.97445446 0.00049832]
 [0.9997093  0.00000002 0.00010198 0.00000571 0.00000174 0.00001787
  0.00009201 0.00000397 0.00002562 0.00004166]
 [0.00049427 0.00000591 0.00000833 0.0000061  0.00000417 0.9934214
  0.00403211 0.0000004  0.00201544 0.00001189]
 [0.00000003 0.0000003  0.00000326 0.00005797 0.00000004 0.00000007
  0.         0.9992471  0.00001087 0.00068034]
 [0.00001496 0.00000557 0.00178513 0.9730356  0.0000012  0.00002986
  0.00000003 0.00000097 0.02507025 0.00005654]
 [0.00000007 0.00000055 0.00000314 0.9982747  0.00000001 0.00168061
  0.         0.00000024 0.00003794 0.00000274]
 [0.00014

...

INFO:tensorflow:global_step/sec: 10.063
INFO:tensorflow:probabilities = [[0.00000006 0.         0.00000004 0.00000074 0.         0.9999472
  0.00001608 0.         0.00002946 0.00000639]
 [0.00011422 0.9942252  0.00107524 0.00023616 0.00060809 0.0000281
  0.00097633 0.00031003 0.00240339 0.00002337]
 [0.00000001 0.00000023 0.00000002 0.00000076 0.99931455 0.00000247
  0.00000021 0.00000057 0.00001811 0.00066304]
 [0.00000037 0.00000015 0.00000573 0.00011037 0.01933849 0.0000067
  0.00000007 0.00037421 0.00004624 0.9801176 ]
 [0.00000042 0.00000153 0.00000795 0.00001053 0.00000768 0.00000343
  0.         0.9995863  0.00000334 0.00037877]
 [0.         0.         0.00000002 0.00000003 0.00000001 0.00000025
  0.         0.9999882  0.00000014 0.0000114 ]
 [0.00000002 0.         0.00000057 0.00002324 0.00030003 0.00004184
  0.         0.00001811 0.00023805 0.9993781 ]
 [0.         0.00000063 0.00000242 0.99958843 0.         0.00039283
  0.         0.00000005 0.00001534 0.00000036]
 [0.0000003

INFO:tensorflow:loss = 0.029450752, step = 39801 (9.936 sec)
INFO:tensorflow:probabilities = [[0.00019184 0.00001844 0.00048971 0.00075857 0.00000826 0.00007684
  0.00004124 0.00000025 0.99838436 0.00003053]
 [0.00000067 0.00000015 0.00000104 0.00000011 0.9998136  0.00000029
  0.00002131 0.00000599 0.00000062 0.00015613]
 [0.00000189 0.9985483  0.00005969 0.00044547 0.00008507 0.00011332
  0.00007886 0.00000902 0.00061709 0.00004124]
 [0.00001386 0.01164359 0.00084435 0.00143801 0.00072128 0.00003373
  0.00010253 0.00002534 0.9850376  0.00013977]
 [0.00000033 0.00000034 0.00266729 0.00141372 0.00000003 0.00000009
  0.         0.9957831  0.00000235 0.0001327 ]
 [0.0001558  0.00109526 0.00479661 0.983062   0.00007982 0.00070694
  0.00000761 0.00061028 0.00452177 0.00496378]
 [0.00000001 0.00000001 0.0000005  0.00000002 0.99966025 0.
  0.00000029 0.00033593 0.00000031 0.00000263]
 [0.00000099 0.99050003 0.00014268 0.00199431 0.00065873 0.00003828
  0.00008591 0.00007378 0.00645669 0.00004

INFO:tensorflow:global_step/sec: 10.6162
INFO:tensorflow:probabilities = [[0.0000067  0.00000446 0.00009139 0.00005694 0.00000456 0.0000457
  0.00000001 0.99120843 0.00001399 0.00856773]
 [0.00000009 0.00000002 0.0000005  0.00005844 0.00001454 0.00000382
  0.         0.00017561 0.00004623 0.9997008 ]
 [0.99983287 0.00000002 0.00001259 0.00000008 0.00000005 0.00004646
  0.00000002 0.00006385 0.00000009 0.00004399]
 [0.00000004 0.00000003 0.00000443 0.00003031 0.00000021 0.00000006
  0.         0.99754876 0.00000725 0.00240895]
 [0.00004006 0.00054048 0.00120727 0.00000065 0.00196702 0.00048391
  0.9955908  0.00000242 0.00010753 0.0000599 ]
 [0.00026861 0.9428418  0.00765147 0.00911511 0.00528272 0.0015877
  0.00623712 0.00397871 0.02184302 0.00119364]
 [0.00004617 0.99694496 0.0005673  0.0000364  0.00011954 0.00000579
  0.00015106 0.00029972 0.00182211 0.00000696]
 [0.00089622 0.9721648  0.0009796  0.00000427 0.00015856 0.00001519
  0.00395892 0.00001789 0.02172357 0.00008101]
 [0.00000

INFO:tensorflow:loss = 0.04952642, step = 39901 (9.419 sec)
INFO:tensorflow:probabilities = [[0.00000338 0.000004   0.00000271 0.00002287 0.00000252 0.99683267
  0.00001283 0.00020121 0.00200701 0.00091073]
 [0.00000452 0.9973341  0.00048997 0.00001803 0.00038768 0.00004128
  0.00002565 0.00001717 0.00167281 0.00000881]
 [0.00154647 0.45138022 0.00042159 0.00077934 0.00165956 0.00078204
  0.00329274 0.00040236 0.53763306 0.00210255]
 [0.00000034 0.000195   0.00000004 0.00002547 0.00106108 0.00001211
  0.00000001 0.00015641 0.00003855 0.9985109 ]
 [0.00000006 0.00000003 0.00000113 0.00000134 0.00000001 0.00000039
  0.         0.9998882  0.00000004 0.00010891]
 [0.         0.00000016 0.00000002 0.00000018 0.9993523  0.00000065
  0.         0.00000213 0.00000438 0.00064023]
 [0.00000012 0.00000006 0.00000207 0.00005765 0.0000091  0.00029935
  0.00000343 0.00000062 0.9996     0.00002769]
 [0.99984217 0.00000001 0.00008268 0.00000124 0.00000001 0.00004734
  0.00000915 0.00000153 0.00000213 

INFO:tensorflow:Saving checkpoints for 40000 into tmp/mnist_convnet_model/model.ckpt.
INFO:tensorflow:Loss for final step: 0.07903315.


In [33]:
# Evaluate the model and print results
eval_input_fn = tf.estimator.inputs.numpy_input_fn(
    x={"x": eval_data},
    y=eval_labels,
    num_epochs=1,
    shuffle=False)
eval_results = mnist_classifier.evaluate(input_fn=eval_input_fn)
print(eval_results)

INFO:tensorflow:Calling model_fn.
INFO:tensorflow:Done calling model_fn.
INFO:tensorflow:Starting evaluation at 2018-11-28-21:25:18
INFO:tensorflow:Graph was finalized.
INFO:tensorflow:Restoring parameters from tmp/mnist_convnet_model/model.ckpt-40000
INFO:tensorflow:Running local_init_op.
INFO:tensorflow:Done running local_init_op.
INFO:tensorflow:Finished evaluation at 2018-11-28-21:25:20
INFO:tensorflow:Saving dict for global step 40000: accuracy = 0.9802, global_step = 40000, loss = 0.06394022
INFO:tensorflow:Saving 'checkpoint_path' summary for global step 40000: tmp/mnist_convnet_model/model.ckpt-40000
{'accuracy': 0.9802, 'loss': 0.06394022, 'global_step': 40000}
